# StandardBayesianMCMCDemo
Standard demo of the Bayesian MCMC calculator

This is a standard demo that can be used with any ROOT file
prepared in the standard way.  You specify:
 - name for input ROOT file
 - name of workspace inside ROOT file that holds model and data
 - name of ModelConfig that specifies details for calculator tools
 - name of dataset

With default parameters the macro will attempt to run the
standard hist2workspace example and read the ROOT file
that it produces.

The actual heart of the demo is only about 10 lines long.

The MCMCCalculator is a Bayesian tool that uses
the Metropolis-Hastings algorithm to efficiently integrate
in many dimensions.  It is not as accurate as the BayesianCalculator
for simple problems, but it scales to much more complicated cases.




**Author:** Kyle Cranmer  
<i><small>This notebook tutorial was automatically generated with <a href= "https://github.com/root-project/root/blob/master/documentation/doxygen/converttonotebook.py">ROOTBOOK-izer</a> from the macro found in the ROOT repository  on Wednesday, April 17, 2024 at 11:20 AM.</small></i>

In [1]:
%%cpp -d

#include "TFile.h"
#include "TROOT.h"
#include "TCanvas.h"
#include "TMath.h"
#include "TSystem.h"
#include "RooWorkspace.h"
#include "RooAbsData.h"

#include "RooStats/ModelConfig.h"
#include "RooStats/MCMCCalculator.h"
#include "RooStats/MCMCInterval.h"
#include "RooStats/MCMCIntervalPlot.h"
#include "RooStats/SequentialProposal.h"
#include "RooStats/ProposalHelper.h"
#include "RooStats/ProposalHelper.h"
#include "RooFitResult.h"

using namespace RooFit;
using namespace RooStats;

struct BayesianMCMCOptions {

   double confLevel = 0.95;
   int intervalType = 2; // type of interval (0 is shortest, 1 central, 2 upper limit)
   double maxPOI = -999; // force different values of POI for doing the scan (default is given value)
   double minPOI = -999;
   int numIters = 100000;    // number of iterations
   int numBurnInSteps = 100; // number of burn in steps to be ignored
};

BayesianMCMCOptions optMCMC;

 Arguments are defined. 

In [2]:
const char *infile = "";
const char *workspaceName = "combined";
const char *modelConfigName = "ModelConfig";
const char *dataName = "obsData";

-------------------------------------------------------
First part is just to access a user-defined file
or create the standard example file if it doesn't exist

In [3]:
const char *filename = "";
if (!strcmp(infile, "")) {
   filename = "results/example_combined_GaussExample_model.root";
   bool fileExist = !gSystem->AccessPathName(filename); // note opposite return code
   // if file does not exists generate with histfactory
   if (!fileExist) {
      // Normally this would be run on the command line
      cout << "will run standard hist2workspace example" << endl;
      gROOT->ProcessLine(".! prepareHistFactory .");
      gROOT->ProcessLine(".! hist2workspace config/example.xml");
      cout << "\n\n---------------------" << endl;
      cout << "Done creating example input" << endl;
      cout << "---------------------\n\n" << endl;
   }

} else
   filename = infile;

Try to open the file

In [4]:
TFile *file = TFile::Open(filename);

if input file was specified byt not found, quit

In [5]:
if (!file) {
   cout << "StandardRooStatsDemoMacro: Input file " << filename << " is not found" << endl;
   return;
}

-------------------------------------------------------
Tutorial starts here
-------------------------------------------------------

get the workspace out of the file

In [6]:
RooWorkspace *w = (RooWorkspace *)file->Get(workspaceName);
if (!w) {
   cout << "workspace not found" << endl;
   return;
}

get the modelConfig out of the file

In [7]:
ModelConfig *mc = (ModelConfig *)w->obj(modelConfigName);

get the modelConfig out of the file

In [8]:
RooAbsData *data = w->data(dataName);

input_line_83:2:2: warning: 'data' shadows a declaration with the same name in the 'std' namespace; use '::data' to reference this declaration
 RooAbsData *data = w->data(dataName);
 ^


make sure ingredients are found

In [9]:
if (!data || !mc) {
   w->Print();
   cout << "data or ModelConfig was not found" << endl;
   return;
}

input_line_84:2:7: error: reference to 'data' is ambiguous
 if (!data || !mc) {
      ^
input_line_83:2:14: note: candidate found by name lookup is 'data'
 RooAbsData *data = w->data(dataName);
             ^
/usr/include/c++/9/bits/range_access.h:318:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/include/c++/9/bits/range_access.h:289:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:299:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:309:5: note: candidate found by name lookup is 'std::data'
    data(_Tp (&__array)[_Nm]) noexcept
    ^


Want an efficient proposal function
default is uniform.

In [10]:
/*

this one is based on the covariance matrix of fit

In [11]:
RooFitResult* fit = mc->GetPdf()->fitTo(*data,Save());
ProposalHelper ph;
ph.SetVariables((RooArgSet&)fit->floatParsFinal());
ph.SetCovMatrix(fit->covarianceMatrix());
ph.SetUpdateProposalParameters(kTRUE); // auto-create mean vars and add mappings
ph.SetCacheSize(100);
ProposalFunction* pf = ph.GetProposalFunction();
*/

this proposal function seems fairly robust

In [12]:
SequentialProposal sp(0.1);

-------------------------------------------------------
create and use the MCMCCalculator
to find and plot the 95% credible interval
on the parameter of interest as specified
in the model config

In [13]:
MCMCCalculator mcmc(*data, *mc);
mcmc.SetConfidenceLevel(optMCMC.confLevel); // 95% interval

input_line_87:2:23: error: reference to 'data' is ambiguous
 MCMCCalculator mcmc(*data, *mc);
                      ^
input_line_83:2:14: note: candidate found by name lookup is 'data'
 RooAbsData *data = w->data(dataName);
             ^
/usr/include/c++/9/bits/range_access.h:318:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/include/c++/9/bits/range_access.h:289:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:299:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:309:5: note: candidate found by name lookup is 'std::data'
    data(_Tp (&__array)[_Nm]) noexcept
    ^


mcmc.SetProposalFunction(*pf);

In [14]:
mcmc.SetProposalFunction(sp);
mcmc.SetNumIters(optMCMC.numIters);             // Metropolis-Hastings algorithm iterations
mcmc.SetNumBurnInSteps(optMCMC.numBurnInSteps); // first N steps to be ignored as burn-in

input_line_89:2:3: error: use of undeclared identifier 'mcmc'
 (mcmc.SetProposalFunction(((*(SequentialProposal*)0x7f617401c000))))
  ^
Error in <HandleInterpreterException>: Error evaluating expression (mcmc.SetProposalFunction(((*(SequentialProposal*)0x7f617401c000))))
Execution of your code was aborted.


default is the shortest interval.

In [15]:
if (optMCMC.intervalType == 0)
   mcmc.SetIntervalType(MCMCInterval::kShortest); // for shortest interval (not really needed)
if (optMCMC.intervalType == 1)
   mcmc.SetLeftSideTailFraction(0.5); // for central interval
if (optMCMC.intervalType == 2)
   mcmc.SetLeftSideTailFraction(0.); // for upper limit

RooRealVar *firstPOI = (RooRealVar *)mc->GetParametersOfInterest()->first();
if (optMCMC.minPOI != -999)
   firstPOI->setMin(optMCMC.minPOI);
if (optMCMC.maxPOI != -999)
   firstPOI->setMax(optMCMC.maxPOI);

MCMCInterval *interval = mcmc.GetInterval();

input_line_90:3:25: error: cannot take the address of an rvalue of type 'RooStats::MCMCInterval::IntervalType'
   mcmc.SetIntervalType(MCMCInterval::kShortest); // for shortest interval (not really needed)
                        ^~~~~~~~~~~~~~~~~~~~~~~
Error while creating dynamic expression for:
  mcmc.SetIntervalType(MCMCInterval::kShortest)


make a plot
TCanvas* c1 =

In [16]:
auto c1 = new TCanvas("IntervalPlot");
MCMCIntervalPlot plot(*interval);
plot.Draw();

TCanvas *c2 = new TCanvas("extraPlots");
const RooArgSet *list = mc->GetNuisanceParameters();
if (list->getSize() > 1) {
   double n = list->getSize();
   int ny = TMath::CeilNint(sqrt(n));
   int nx = TMath::CeilNint(double(n) / ny);
   c2->Divide(nx, ny);
}

input_line_91:7:1: warning: 'list' shadows a declaration with the same name in the 'std' namespace; use '::list' to reference this declaration
const RooArgSet *list = mc->GetNuisanceParameters();
^
[runStaticInitializersOnce]: Failed to materialize symbols: { (main, { __cxx_global_var_initcling_module_483_.5, __cxx_global_var_initcling_module_483_.9, __vd_init_order__cling_Un1Qu35, _ZN12__cling_N5324listE, _ZNK16RooAbsCollection7getSizeEv, __cxx_global_var_initcling_module_483_.7, _ZN13RooStringViewC2ERKNSt7__cxx1112basic_stringIcSt11char_traitsIcESaIcEEE, _ZN12__cling_N53216__cling_Un1Qu341EPv, _ZN12__cling_N5322c1E, __cxx_global_var_initcling_module_483_.2, _ZN12__cling_N53224__dynamic__cling_Un1Qu30E, _ZN12__cling_N5324plotE, _ZN13RooStringViewC1ERKNSt7__cxx1112basic_stringIcSt11char_traitsIcESaIcEEE, __orc_init_func.cling-module-483, _ZNKSt6vectorIP9RooAbsArgSaIS1_EE4sizeEv, __cxx_global_var_initcling_module_483_.6, _ZN5TMath4NintIdEEiT_, $.cling-module-483.__inits.0, _ZNK8RooStats

draw a scatter plot of chain results for poi vs each nuisance parameters

In [17]:
int iPad = 1; // iPad, that's funny
for (auto *nuis : static_range_cast<RooRealVar *>(*mc->GetNuisanceParameters())) {
   c2->cd(iPad++);
   plot.DrawChainScatter(*firstPOI, *nuis);
}

[runStaticInitializersOnce]: Failed to materialize symbols: { (main, { __orc_init_func.cling-module-483 }) }
cling JIT session error: Failed to materialize symbols: { (main, { _ZNK8RooStats11ModelConfig21GetNuisanceParametersEv }) }


print out the interval on the first Parameter of Interest

In [18]:
cout << "\n>>>> RESULT : " << optMCMC.confLevel * 100 << "% interval on " << firstPOI->GetName() << " is : ["
     << interval->LowerLimit(*firstPOI) << ", " << interval->UpperLimit(*firstPOI) << "] " << endl;

gPad = c1;

cling JIT session error: Failed to materialize symbols: { (main, { _ZN12__cling_N5322c1E }) }


Draw all canvases 

In [19]:
%jsroot on
gROOT->GetListOfCanvases()->Draw()